In [164]:
import geopandas as gpd
from pathlib import Path
from shapely.geometry import Polygon
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt

In [64]:
PREPROCESSED_DATA_PATH = Path("~/Library/Mobile Documents/com~apple~CloudDocs/MIT/6.C35")
PREPROCESSED_DATA_PATH

PosixPath('~/Library/Mobile Documents/com~apple~CloudDocs/MIT/6.C35')

In [65]:
parcels_within_station_buffer = gpd.read_file(PREPROCESSED_DATA_PATH / 'station_only_parcels.geojson')

In [45]:
selected_columns = ['LOC_ID', 'TOWN_NAME', 'USE_CODE', 'LOCATION', 'CITY', 'ZONING', 'STYLE', 'stop_name', 'geometry']

In [83]:
sum(pd.to_numeric(parcels_within_station_buffer['UNITS'], errors='coerce').dropna())

292369.0

In [166]:
selected_columns = ['LOC_ID', 'TOWN_NAME', 'USE_CODE', 'LOCATION', 'CITY', 'ZONING', 'STYLE', 'stop_name', 'geometry', 'LOT_SIZE', 'UNITS']

#these are for brookline, will need to see if they scale https://www.brooklinema.gov/DocumentCenter/View/19956/GIS---Zoning-Map-10CC-11x17pdf
sf_zoning_codes = ['S-40', 'S-25', 'S-15', 'S-10', 'S-7', 'S-4', 'S-0.5P,' 'S-0.75P', 'SC-7', 'SC-10', 'T-6', 'T-5', 'SF', 'S10', 'S40', 'S25', 'S15', 'S7', 'S4']
multifamily_zoning_codes = ['F10', 'M-0.5', 'M5', 'M10', 'M10(CAM)', 'M15', 'M20', 'M25'] #the zoning code says M1.0, M1.5, but the data has it has M10, M15, etc.
commercial_zoning_codes = ['L-0.5', 'L-0.5(CL)', 'L-1.0', 'G-1.0', 'G-(DP)', 'G-1.75(CC)', 'G-1.75(LSH)', 'G-1.75(WS)', 'G-2.0', 'G-2.0(CA)', 'GMR-2.0', 'O-1.0', 
                           'O-2.0(CH)', 'G175(LSH', 'G10', 'G20', 'G175(WS)', 'G175(CC)', 'G(DP)', 'G', 'GU', 'GR','GB', 'GI', 'G RS', 'GC', 'GBD', 'GD', 'G20', 'G175(CC)', 
                           'G175(WS)', 'G175(LSH', 'G10', 'GMR20', 'G(DP)', 'GRA', 'GRB'] 


def get_pct_sf_zoning(community_df: pd.DataFrame) -> float:
    # “Multi-family housing” means a building with 3 or more residential dwelling units or 
    # 2 or more buildings on the same lot with more than 1 residential dwelling unit in each building.
    # Based on this I am including duplex zoning in the designation of area that would need to be upzoned
    
    pct_sfzoning_parcels = len(community_df[community_df["ZONING"].isin(sf_zoning_codes)])/len(community_df) # TODO: review zoning codes and make sure this is the only one
    return round(pct_sfzoning_parcels*100, 2)


def get_pct_multifamily_zoning(community_df: pd.DataFrame) -> float:

    pct_multifamily_zoning_parcels = len(community_df[(community_df["ZONING"].isin(multifamily_zoning_codes))])/len(community_df)
    return round(pct_multifamily_zoning_parcels*100, 2)

def get_pct_commercial_zoning(community_df: pd.DataFrame) -> float:

    pct_commercial_zoning_parcels = len(community_df[(community_df["ZONING"].isin(commercial_zoning_codes))])/len(community_df)
    return round(pct_commercial_zoning_parcels*100, 2)


def get_pct_multifamily_usage(community_df: pd.DataFrame) -> float:

    pct_multifamily_zoning_parcels = len(community_df[(community_df["USE_CODE"] < 115) & (community_df["USE_CODE"] > 105)])/len(community_df)
    return round(pct_multifamily_zoning_parcels*100, 2)

def get_pct_commercial_usage(community_df: pd.DataFrame) -> float:

    pct_commercial_zoning_parcels = len(community_df[(community_df["USE_CODE"] < 400) & (community_df["USE_CODE"] > 300)])/len(community_df)
    return round(pct_commercial_zoning_parcels*100, 2)

def get_pct_sf_use(community_df: pd.DataFrame) -> float:
    #TODO: include 104 for 2 family dwelling?
    pct_sfuse_parcels = len(community_df[community_df["USE_CODE"] == '101'])/len(community_df) 
    return round(pct_sfuse_parcels*100, 2)


def get_current_density(parcels_within_station_buffer):
    # MBTA CA requires 15 units per acre
    # density = number of units/total developable parcel area
    total_units = sum(pd.to_numeric(parcels_within_station_buffer['UNITS'], errors='coerce').dropna())
    total_land_area = sum(pd.to_numeric(parcels_within_station_buffer['LOT_SIZE'], errors='coerce').dropna())

    return total_units/total_land_area
    



def get_median_lot_size():
    #TODO: These seem like acres.
    return pd.to_numeric(parcels_within_station_buffer['LOT_SIZE']).median()


# def get_median_property_value():
    

    

In [158]:
notnone = [parcel for parcel in parcels_within_station_buffer["ZONING"].unique() if parcel is not None]
G_records = [record for record in notnone if record.startswith('G')]
G_records


['G',
 'GU',
 'GR',
 'GB',
 'GI',
 'G RS',
 'GC',
 'GBD',
 'GD',
 'G20',
 'G175(CC)',
 'G175(WS)',
 'G175(LSH',
 'G10',
 'GMR20',
 'G(DP)',
 'GRA',
 'GRB']

In [ ]:
def visualize_land_use_distribution_of_station_area()
    

def visualize_zoning_distribution_of_station_area(community_df):
    

    df_long = pd.melt(community_df, id_vars='Community_Name', var_name='Category', value_name='Percentage')

    # Create the stacked bar chart using Seaborn
    plt.figure(figsize=(10, 6))
    sns.barplot(data=df_long, x='city', y='Percentage', hue='Category', palette='pastel', edgecolor='grey')

    # Add labels and title
    plt.xlabel('City')
    plt.ylabel('Percentage')
    plt.title('Parcel Usage Breakdown by T Stop: Brookline, MA')

    # Show plot
    plt.xticks(rotation=45)
    plt.legend(title='Category')
    plt.tight_layout()
    plt.show()


In [151]:
parcel_usage = []
for stop in parcels_within_station_buffer[parcels_within_station_buffer['TOWN_NAME'] == 'Brookline']["stop_name"].unique():
    stop_df = parcels_within_station_buffer[parcels_within_station_buffer["stop_name"] == stop]
    {'mbta_stop', stop, 
     "% SF usage", get_pct_sf_use(stop_df), 
     "% multifamily usage", get_pct_multifamily_usage(stop_df)}

    # print('stop: ', stop, "% SF zoning", get_pct_sf_zoning(stop_df), "% multifamily", get_pct_multifamily_zoning(stop_df))
    # print('stop: ', stop, "zoning types: ", stop_df["ZONING"].unique())
    



stop:  Hawes Street zoning types:  ['S-7' 'M20' 'G20' None 'M15' 'L10' 'SC7' 'M10' 'F-1' 'G175(CC)' 'T-5'
 'S10']
stop:  Kent Street zoning types:  ['S-7' 'M20' 'G20' None 'M15' 'L10' 'SC7' 'T-5' 'M10' 'F-1' 'G175(CC)'
 'S10' 'G175(LSH']
stop:  Longwood zoning types:  ['S-7' 'M20' None 'M15' 'L10' 'SC7' 'T-5' 'S10' 'M10' 'G175(CC)']
stop:  Saint Mary's Street zoning types:  ['S-7' 'M20' 'G20' None 'M15' 'L10' 'SC7' 'M10' 'T-5' 'S10']
stop:  Saint Paul Street zoning types:  ['M20' 'S-7' None 'SC7' 'T-5' 'M15' 'M10' 'F-1' 'G175(CC)' 'L10' 'S10'
 'G175(LSH']
stop:  Coolidge Corner zoning types:  ['SC7' 'T-5' 'S-7' 'M15' None 'F-1' 'M10' 'M20' 'G175(CC)' 'L10' 'T-6'
 'M25' 'S10' 'G175(LSH' 'G20' 'L05']
stop:  Summit Avenue zoning types:  ['M15' None 'F-1' 'M20' 'G175(CC)' 'T-5' 'M10' 'L10' 'T-6' 'S-7'
 'G175(WS)' 'SC7' 'M25' 'G175(LSH' 'G20' 'L05' 'G10' 'SC10']
stop:  Brandon Hall zoning types:  ['M20' 'G175(CC)' None 'M10' 'T-5' 'L10' 'T-6' 'S-7' 'F-1' 'G175(WS)'
 'M15' 'SC7' 'M25' 'G175(

### Coolidge Corner Stats

In [160]:
parcels_within_station_buffer_brookline_cc = parcels_within_station_buffer[parcels_within_station_buffer["stop_name"] == 'Coolidge Corner']

parcels_within_station_buffer_brookline_cc = parcels_within_station_buffer_brookline_cc[selected_columns]

print('% sf zoning', get_pct_sf_zoning(parcels_within_station_buffer_brookline_cc))
print('% sf use', get_pct_sf_use(parcels_within_station_buffer_brookline_cc))
print('% multifamily zoning', get_pct_multifamily_zoning(parcels_within_station_buffer_brookline_cc))
print('% commercial zoning', get_pct_commercial_zoning(parcels_within_station_buffer_brookline_cc))

print('current housing density (units/acre)', get_current_density(parcels_within_station_buffer_brookline_cc))

% sf zoning 13.57
% sf use 8.19
% multifamily zoning 10.87
% commercial zoning 1.15
current housing density (units/acre) 45.104982502916144


#### Washington Square Stats

In [162]:
parcels_within_station_buffer_brookline_ws = parcels_within_station_buffer[parcels_within_station_buffer["stop_name"] == 'Washington Square']
parcels_within_station_buffer_brookline_ws = parcels_within_station_buffer_brookline_ws[selected_columns]


print('% sf zoning', get_pct_sf_zoning(parcels_within_station_buffer_brookline_ws))
print('% sf use', get_pct_sf_use(parcels_within_station_buffer_brookline_ws))
print('% multifamily zoning', get_pct_multifamily_zoning(parcels_within_station_buffer_brookline_ws))

print('% commercial zoning', get_pct_commercial_zoning(parcels_within_station_buffer_brookline_ws))

print('current housing density (units/acre)', get_current_density(parcels_within_station_buffer_brookline_ws))



% sf zoning 25.09
% sf use 19.9
% multifamily zoning 15.61
% commercial zoning 1.23
current housing density (units/acre) 24.400417101147106


In [123]:
parcels_within_station_buffer_brookline_ws["ZONING"].unique()
# | (parcels_within_station_buffer_brookline_ws["ZONING"] == 'R-2')])
# /len(parcels_within_station_buffer_brookline_ws) 

array(['S-7', None, 'T-5', 'T-6', 'M20', 'G175(WS)', 'M15', 'SC7',
       'G175(CC)', 'M10', 'M25', 'SC10', 'S10'], dtype=object)

In [48]:
parcels_within_station_buffer_brookline_cc.explore()